In [59]:
import os
os.chdir('/Neural Text Summarization/project/codes')

In [60]:
import numpy as np
from collections import Counter
import numpy as np
import math
import torch
import torch.nn as nn
import random
import time
import io
import codecs

import rougee
#from extractor_cos import PacSumExtractorWithBert, PacSumExtractorWithTfIdf
from data_iterator import Dataset
import rougee

In [61]:
class PacSumExtractorWithTfIdf():

    #def __init__(self, extract_num = 3, beta = 3, lambda1 = -0.2, lambda2 = -0.2):

        #super(PacSumExtractorWithTfIdf, self).__init__(extract_num, beta, lambda1, lambda2)

    def _calculate_similarity_matrix(self, doc):
        #print('doc:')
        #print(doc)
        

        idf_score = self._calculate_idf_scores(doc)
        #print('idf_score:')
        #print(idf_score)

        tf_scores = [
            Counter(sentence) for sentence in doc
        ]
        #print('tf_score:')
        #print(tf_scores)
        length = len(doc)
        #print('doc_length:')
        #print(len(doc))

        similarity_matrix = np.zeros([length] * 2)

        for i in range(length):
            for j in range(i, length):
                similarity = self._idf_modified_dot(tf_scores, i, j, idf_score)

                if similarity:
                    similarity_matrix[i, j] = similarity
                    similarity_matrix[j, i] = similarity

        return similarity_matrix


    def _idf_modified_dot(self, tf_scores, i, j, idf_score):
        
        #print('tf_scores')
        #print(tf_scores)
        #print('idf_score')
        #print(idf_score)

        idf_vec = np.zeros(2)
        x = 0
        if i == j:
            return 1

        tf_i, tf_j = tf_scores[i], tf_scores[j]
        words_i, words_j = set(tf_i.keys()), set(tf_j.keys())
        
        score = 0

        for word in words_i & words_j:
            
            idf = idf_score[word]
            #idf_vec[x] = idf
            
            #Cosine similarity
            score += ((tf_i[word] * tf_j[word] * idf ** 2)/(np.sqrt(tf_i[word]**2+idf**2)*np.sqrt(tf_i[word]**2+idf**2)))
            
            #x = x+1
        
        #cos_score = score/((np.sqrt(tf_i**2 + idf_vec[0]**2)) * (np.sqrt(tf_j**2 + idf_vec[1]**2)))


        return score


    def _calculate_idf_scores(self, doc):

        doc_number_total = 0.
        df = {}
        for i, sen in enumerate(doc):
            tf = Counter(sen)
            for word in tf.keys():
                if word not in df:
                    df[word] = 0
                df[word] += 1
            doc_number_total += 1

        idf_score = {}
        for word, freq in df.items():
            idf_score[word] = math.log(doc_number_total - freq + 0.5) - math.log(freq + 0.5)

        return idf_score

In [62]:
rouge = rougee.Rouge()

In [63]:
tune_dataset = Dataset('/Neural Text Summarization/project/data/CNN_DM/cd.validation.h5df')
tune_dataset_iterator = tune_dataset.iterate_once_doc_tfidf()

input max len : 60


In [64]:
extractor = PacSumExtractorWithTfIdf()

In [65]:
def _select_tops(edge_scores, beta, lambda1, lambda2):

        min_score = edge_scores.min()
        max_score = edge_scores.max()
        edge_threshold = min_score + beta * (max_score - min_score)
        new_edge_scores = edge_scores - edge_threshold
        forward_scores, backward_scores, _ = _compute_scores(new_edge_scores, 0)
        forward_scores = 0 - forward_scores

        paired_scores = []
        for node in range(len(forward_scores)):
            paired_scores.append([node,  lambda1 * forward_scores[node] + lambda2 * backward_scores[node]])

        #shuffle to avoid any possible bias
        random.shuffle(paired_scores)
        paired_scores.sort(key = lambda x: x[1], reverse = True)
        extracted = [item[0] for item in paired_scores[:3]]


        return extracted

def _compute_scores(similarity_matrix, edge_threshold):

    forward_scores = [0 for i in range(len(similarity_matrix))]
    backward_scores = [0 for i in range(len(similarity_matrix))]
    edges = []
    for i in range(len(similarity_matrix)):
        for j in range(i+1, len(similarity_matrix[i])):
            edge_score = similarity_matrix[i][j]
            if edge_score > edge_threshold:
                forward_scores[j] += edge_score
                backward_scores[i] += edge_score
                edges.append((i,j,edge_score))

    return np.asarray(forward_scores), np.asarray(backward_scores), edges

In [66]:
def _tune_extractor(edge_scores):

        tops_list = []
        hparam_list = []
        num = 10
        for k in range(num + 1):
            beta = k / num
            for i in range(11):
                lambda1 = i/10
                lambda2 = 1 - lambda1
                extracted = _select_tops(edge_scores, beta=beta, lambda1=lambda1, lambda2=lambda2)

                tops_list.append(extracted)
                hparam_list.append((beta, lambda1, lambda2))

        return tops_list, hparam_list

In [67]:
example_num=1000


summaries, references = [], []
k = 0
for item in tune_dataset_iterator:
    
    article, abstract, inputs = item
    edge_scores =extractor._calculate_similarity_matrix(*inputs)
    tops_list, hparam_list = _tune_extractor(edge_scores)

    summary_list = [list(map(lambda x: article[x], ids)) for ids in tops_list]
    summaries.append(summary_list)
    references.append([abstract])
    k += 1
    print(k)
    if k % example_num == 0:
        break

Processing file: C:/WS 2019/Neural Text Summarization/project/data/CNN_DM/cd.validation.h5df
1
2
3
4
5
6
7
8
9
10
11
12
13
14
15
16
17
18
19
20
21
22
23
24
25
26
27
28
29
30
31
32
33
34
35
36
37
38
39
40
41
42
43
44
45
46
47
48
49
50
51
52
53
54
55
56
57
58
59
60
61
62
63
64
65
66
67
68
69
70
71
72
73
74
75
76
77
78
79
80
81
82
83
84
85
86
87
88
89
90
91
92
93
94
95
96
97
98
99
100
101
102
103
104
105
106
107
108
109
110
111
112
113
114
115
116
117
118
119
120
121
122
123
124
125
126
127
128
129
130
131
132
133
134
135
136
137
138
139
140
141
142
143
144
145
146
147
148
149
150
151
152
153
154
155
156
157
158
159
160
161
162
163
164
165
166
167
168
169
170
171
172
173
174
175
176
177
178
179
180
181
182
183
184
185
186
187
188
189
190
191
192
193
194
195
196
197
198
199
200
201
202
203
204
205
206
207
208
209
210
211
212
213
214
215
216
217
218
219
220
221
222
223
224
225
226
227
228
229
230
231
232
233
234
235
236
237
238
239
240
241
242
243
244
245
246
247
248
249
250
251
252
253
254

In [91]:
count = 0
best_rouge = 0
best_hparam = None
for i in range(len(summaries[0])):
    print(i)
    print("threshold :  "+str(hparam_list[i])+'\n')
    #print("non-lead ratio : "+str(ratios[i])+'\n')
    for k in range(len(summaries)):
        #print(i)
        print(k)
        summ = summaries[k][i]
        #print('summ')
        #print(len(summ))
        #print(summaries)
        ref = references[k][0]
        
        if len(summ) == len(ref):
            count = count + 1
            
            print('sum')
            print(len(summ))
            if i != 8 and i != 10:
                if summaries[k][i][0]!='.' and summaries[k][i][1]!='.' and summaries[k][i][2]!='.':
                    result = rouge.get_scores(summ, ref, avg = True)
                    
                    #print(result)
                    if result['rouge-1']['f'] > best_rouge:
                        best_rouge = result['rouge-1']['f']
                        best_hparam = hparam_list[i]

print("The best hyper-parameter :  beta %.4f , lambda1 %.4f, lambda2 %.4f " % (best_hparam[0], best_hparam[1], best_hparam[2]))
print("The best rouge_1_f_score :  %.4f " % best_rouge)

beta = best_hparam[0]
lambda1 = best_hparam[1]
lambda2 = best_hparam[2]

0
threshold :  (0.0, 0.0, 1.0)

0
sum
3
1
2
3
4
5
6
7
8
9
10
11
12
sum
3
13
14
15
16
17
18
19
sum
3
20
sum
3
21
22
sum
3
23
24
sum
3
25
sum
3
26
27
28
29
30
31
32
33
34
35
36
37
38
39
40
41
sum
3
42
43
sum
3
44
sum
3
45
46
47
48
49
sum
3
50
sum
3
51
52
53
54
55
sum
3
56
57
sum
3
58
59
sum
3
60
61
62
63
sum
3
64
sum
3
65
sum
3
66
67
68
69
sum
3
70
71
72
73
sum
3
74
75
sum
3
76
77
78
79
80
81
82
83
84
85
86
sum
3
87
88
sum
3
89
90
91
92
93
94
95
96
97
98
99
100
101
sum
3
102
103
104
105
sum
3
106
107
108
109
110
111
112
113
114
115
sum
3
116
117
sum
3
118
sum
3
119
120
sum
3
121
122
sum
3
123
124
125
sum
3
126
sum
3
127
128
sum
3
129
130
131
132
133
134
135
136
sum
3
137
138
sum
3
139
140
141
sum
3
142
143
sum
3
144
145
sum
3
146
147
sum
3
148
sum
3
149
150
151
sum
3
152
sum
3
153
154
155
156
sum
3
157
158
sum
3
159
sum
3
160
sum
3
161
162
sum
3
163
sum
3
164
165
166
167
sum
3
168
169
sum
3
170
171
172
173
174
175
176
177
178
179
sum
3
180
181
sum
3
182
sum
3
183
184
sum
3
185
sum
3
186


In [92]:
print("The best hyper-parameter :  beta %.4f , lambda1 %.4f, lambda2 %.4f " % (best_hparam[0], best_hparam[1], best_hparam[2]))
print("The best rouge_1_f_score :  %.4f " % best_rouge)

beta = best_hparam[0]
lambda1 = best_hparam[1]
lambda2 = best_hparam[2]

The best hyper-parameter :  beta 1.0000 , lambda1 0.8000, lambda2 0.2000 
The best rouge_1_f_score :  0.6946 


In [93]:
#testing
test_dataset = Dataset('C:/WS 2019/Neural Text Summarization/project/data/CNN_DM/cd.test.h5df')
test_dataset_iterator = test_dataset.iterate_once_doc_tfidf()

input max len : 60


In [94]:
#Extract summary
from collections import Counter
import numpy as np
import math
import torch
import torch.nn as nn
import random
import time
import io
import codecs

extract_num = 3
summaries_test = []
references_test = []

for item in test_dataset_iterator:
    article, abstract, inputs = item
    if len(article) <= extract_num and len(article) == len(abstract):
        summaries.append(article)
        references.append([abstract])
        continue

    edge_scores = extractor._calculate_similarity_matrix(*inputs)
    ids = _select_tops(edge_scores = edge_scores, beta=0, lambda1=0, lambda2=1)
    summary = list(map(lambda x: article[x], ids))
    summaries_test.append(summary)
    references_test.append([abstract])

Processing file: C:/WS 2019/Neural Text Summarization/project/data/CNN_DM/cd.test.h5df


In [95]:
new_score = 0
score = 0
for i in range (0,5000):
    print(i)
    for k in range (len(summaries_test[0])):
        if len(summaries_test[i]) == len(summaries_test[0]) and summaries_test[i][k]!= '.':
            new_score = rouge.get_scores(summaries_test[i][k], references_test[i][0][0])
            R_L_f = new_score[0]['rouge-l']['f']
            score = (score + R_L_f)

0
hyp:
['this month , kim and her husband kanye west made a high-profile tour of armenia and israel to baptise their daughter and retrace the kardashian roots']
ref
["kim and kanye west recently visited armenia to retrace her family 's roots"]
hyp:
['this month , kim and her husband kanye west made a high-profile tour of armenia and israel to baptise their daughter and retrace the kardashian roots']
ref
["kim and kanye west recently visited armenia to retrace her family 's roots"]
hyp:
['this month , kim and her husband kanye west made a high-profile tour of armenia and israel to baptise their daughter and retrace the kardashian roots']
ref
["kim and kanye west recently visited armenia to retrace her family 's roots"]
hyp:
['while the famous kardashian used to pick holidays close to home , in the sun , on a beach and with her family - if her recent vacations are anything to go by - times have changed']
ref
["kim and kanye west recently visited armenia to retrace her family 's roots"]
h

In [96]:
score/5000

0.5314464939171467